## Locally Optimal Block Preconditioned Conjugate Gradient (LOBPCG)

### Kirchoff-Love plate equation with axial load:

\begin{align}
D \Delta^{2}w - N_{x}\frac{\partial^{2} w}{\partial x^{2}} = 0,
\end{align}

#### with clamped boundary conditions

### weak Form:

\begin{align}
\int_{\Omega} D \nabla^{2}w:\nabla v dx + N_{x}\int_{\Omega} w^{'}v^{'}dx =0
\end{align}


### HHJ method for Kirchhoff-Love plate equation:

\begin{align}
\sigma = D \nabla^{2}w \quad \Rightarrow \quad D^{-1} \sigma = \nabla^{2}w,
\end{align}


Find $(w,\sigma)\in H_{0}^{1}(\Omega)\times H(divdiv,\Omega)$ such that $(v,\tau)\in H_{0}^{1}(\Omega)\times H(divdiv,\Omega)$,

\begin{align}
\int_{\Omega} D^{-1} \sigma:\tau  + <div(\tau),\nabla w>_{H(curl)\times H(curl)} dx = 0
\end{align}


\begin{align}
\int_{\Omega}   <div(\sigma),\nabla w>_{H(curl)\times H(curl)} + N_{x}\int_{\Omega} w^{'}v^{'}dx = 0
\end{align}

In [ ]:
from ngsolve import *
from ngsolve.webgui import Draw
from ngsolve.meshes import MakeStructured2DMesh
from ngsolve.la import EigenValues_Preconditioner
import numpy as np
import math
import scipy.linalg
from random import random
import scipy.sparse as sp

In [ ]:
L = 1
mesh = MakeStructured2DMesh(quads=True, nx=50,ny=50, mapping= lambda x,y : (L*(-1+2*x),L*(-1+2*y)))
Draw(mesh)

In [ ]:
E  = 1e4
nu = 0.3
t  = 1e-2#1e-4#1e-2
D  = (E*t**3)/(12*(1-nu**2))

In [ ]:
def MaterialInv(mat):
    return 1/D*(1/(1-nu)*mat-nu/(1-nu**2)*Trace(mat)*Id(2))

In [ ]:
V = HDivDiv(mesh, order=1)
Q = H1(mesh, order=2, dirichlet=".*")
w, v = Q.TnT()
sigma, tau = V.TnT()

In [ ]:
n = specialcf.normal(2)

def tang(u): return u-(u*n)*n

a = BilinearForm( InnerProduct (MaterialInv(sigma), tau)*dx ).Assemble()

b = BilinearForm(div(tau)*grad(w)*dx + (- (tau*n)*tang(grad(w)))*dx(element_boundary=True)).Assemble()


k = BilinearForm(grad(w)*grad(v)*dx).Assemble()

S = b.mat.T @ a.mat.Inverse() @ b.mat
print (S.GetOperatorInfo())

pre = k.mat.Inverse(Q.FreeDofs())
pre = pre@pre   # precond for 4th order problem

evals, evecs = solvers.LOBPCG(S, k.mat, pre=pre, num=5, maxit=600)

In [ ]:
#400  iterations: 0.015425633998942216, 0.02226002048401675, 0.02355176645996107, 0.03271232421187974, 0.1467672697089979
#500  iterations: 0.013506467277142602, 0.02169684549221822, 0.02217515442488544, 0.03101180291418709, 0.0858424064805721
#750  iterations: 0.011988345348758096, 0.02114812492544892, 0.02125181877898747, 0.03804422088636883, 0.0583182100792465
#1000 iterations: 0.012008665627107276, 0.02111039625024922, 0.02112271954676164, 0.02942628005316644, 0.0413753010792073

In [ ]:
print("eigen values: ", evals)

In [ ]:
# draw eigen functions
gfu = GridFunction(Q)
for i in range(len(evecs)):
    gfu.vec.data = evecs[i]
    Draw(gfu, deformation=True)